In [1]:
from pymongo import MongoClient
from dotenv import load_dotenv
import os

load_dotenv()

mongo_connection_string = os.getenv("MONGO_CONNECTION_STRING")

client = MongoClient(mongo_connection_string) 
db = client['lingwing']  
collection = db['your_collection_name']  # Replace with your collection name

In [2]:
collection = db['usercourses']

In [3]:
from pymongoarrow.schema import Schema
import pymongoarrow
import pyarrow as pa

user_course_schema = Schema({
    'startDate': pa.timestamp('ms'),
    'endDate': pa.timestamp('ms'),
    'ended': pa.bool_(),
    'certificate': pa.bool_(),
    'countryCode': pa.string(),
    'course': pymongoarrow.types.ObjectIdType(),
    'courseSlug': pa.string(),
    'score': pa.int32(),
    'sentTasksCount': pa.int32(),
    'shouldBeSent': pa.int32(),
    'uniquePassedTasks': pa.int32(),
    'reloaded': pa.bool_(),
    'totalWrongAnswers': pa.int32(),
    'totalRightAnswers': pa.int32(),
    'uniqueTasksRightAnswers': pa.int32(),
    'uniqueTasksWrongAnswers': pa.int32(),
    'totalTimeSpent': pa.int64(),
    'iLearnFromNameCode': pa.string(),
    'heart': pa.struct([
        ('count', pa.int32()),
        ('temporaryScore', pa.int32())
    ]),
    'allPassedTasks': pa.int32(),
    'reachedDailyLimit': pa.bool_(),
    'passedReplayPoints': pa.int32(),
    'percent': pa.string(),
    'oldUserCourseId': pymongoarrow.types.ObjectIdType(),
    'oldEnded': pa.bool_(),
    'oldCertificate': pa.bool_(),
    'replayTasksObjectIds': pa.list_(pymongoarrow.types.ObjectIdType()),
    'lastSentTaskIds': pa.list_(pymongoarrow.types.ObjectIdType()),
    'sentDailyTaskCounter': pa.int32(),
    'dailyReachedLimitDate': pa.timestamp('ms'),
    'vote': pa.struct([
        ('voted', pa.bool_()),
        ('amount', pa.int32())
    ]),
    'rating': pa.struct([
        ('total', pa.string()),
        ('task', pa.struct([
            ('mistake', pa.string()),
            ('time', pa.string())
        ]))
    ]),
    'docInfo': pa.struct([
        ('createDate', pa.timestamp('ms')),
        ('user', pymongoarrow.types.ObjectIdType()),
        ('unRegisteredUser', pymongoarrow.types.ObjectIdType())
    ]),
    'delete': pa.struct([
        ('isDeleted', pa.string()),
        ('deleteDate', pa.timestamp('ms')),
        ('user', pymongoarrow.types.ObjectIdType())
    ]),
    'statistics': pa.struct([
        ('daily', pa.list_(pa.struct([
            ('date', pa.timestamp('ms')),
            ('rating', pa.struct([
                ('total', pa.string()),
                ('task', pa.struct([
                    ('mistake', pa.string()),
                    ('time', pa.string())
                ]))
            ]))
        ]))),
        ('lastWeekDate', pa.timestamp('ms')),
        ('lastWeekRating', pa.int32()),
        ('previousWeekDate', pa.timestamp('ms')),
        ('previousWeekRating', pa.int32()),
        ('weekly', pa.list_(pa.struct([
            ('date', pa.timestamp('ms')),
            ('rating', pa.struct([
                ('total', pa.string()),
                ('task', pa.struct([
                    ('mistake', pa.string()),
                    ('time', pa.string())
                ]))
            ]))
        ]))),
        ('latest', pa.struct([
            ('date', pa.timestamp('ms')),
            ('rating', pa.struct([
                ('total', pa.string()),
                ('task', pa.struct([
                    ('mistake', pa.string()),
                    ('time', pa.string())
                ]))
            ]))
        ]))
    ]),
    'learnMode': pa.int32(),
    'userCourseType': pa.int32(),
    'maxTestTaskCount': pa.int32(),
    'freeTest': pa.bool_(),
    'stats': pa.string(),
    'tasks': pa.list_(pa.string()),
    'passedTasks': pa.list_(pa.struct([
        ('taskId', pymongoarrow.types.ObjectIdType()),
        ('sequentialNumber', pa.int32()),
        ('mistake', pa.struct([
            ('sum', pa.int32()),
            ('hint', pa.int32()),
            ('audio', pa.int32()),
            ('typo', pa.int32()),
            ('check', pa.int32())
        ])),
        ('score', pa.int32()),
        ('wholeScore', pa.int32()),
        ('timeSpent', pa.int32()),
        ('wholeTimeSpent', pa.int32())
    ]))
})


In [4]:
from pymongoarrow.api import find_arrow_all

query = {}  # An empty query fetches all documents
arrow_table = find_arrow_all(collection, query, schema=user_course_schema)

# Convert to pandas DataFrame
df = arrow_table.to_pandas()


ArrowNotImplementedError: Not implemented type for Arrow list to pandas: fixed_size_binary[12]

In [7]:
# Example for converting 'course' field from ObjectId to string

for i in range(len(arrow_table)):
    arrow_table['course'][i] = str(arrow_table['course'][i].as_py())


TypeError: 'pyarrow.lib.ChunkedArray' object does not support item assignment

In [9]:
df = old_arrow_table.to_pandas()

ArrowNotImplementedError: Not implemented type for Arrow list to pandas: fixed_size_binary[12]

In [ ]:
df.to_csv('users-courses.csv', index=False)

In [10]:
arrow_table = old_arrow_table

In [10]:
#copy_df = df

In [16]:
df = copy_df

In [17]:
import pandas as pd

def normalize_column(df, col, prefix):
    """ Normalizes a column with potentially nested data """
    # Create an empty DataFrame for normalized data
    normalized_df = pd.DataFrame()

    for i, row in df.iterrows():
        # Extract the data for the current column
        data = row[col]

        # Check the data type and normalize accordingly
        if isinstance(data, list):
            # Normalize each item in the list and concatenate
            normalized_list = pd.concat([pd.json_normalize(item) for item in data if item is not None], sort=False).reset_index(drop=True)
            normalized_list = normalized_list.add_prefix(f"{prefix}.")
            normalized_df = pd.concat([normalized_df, normalized_list], sort=False)
        elif isinstance(data, dict):
            # Normalize the dictionary
            normalized_dict = pd.json_normalize(data)
            normalized_dict = normalized_dict.add_prefix(f"{prefix}.")
            normalized_df = pd.concat([normalized_df, normalized_dict], sort=False)
        else:
            # Handle non-dict and non-list data types
            normalized_df = pd.concat([normalized_df, pd.DataFrame([{f"{prefix}": data}])], sort=False)

    # Reset index for consistency
    normalized_df.reset_index(drop=True, inplace=True)
    return pd.concat([df.reset_index(drop=True), normalized_df], axis=1)

# Apply normalization to each nested column
nested_cols = ['freeTrial', 'local', 'facebook', 'google', 'twitter', 'info', 'profile', 'emailLogs', 'smsLogs', 'delete', 'tutorial', 'creditCard']
for col in nested_cols:
    df = normalize_column(df, col, col)
    df.drop(columns=[col], inplace=True)

# Handle sub-nested fields similarly if needed

# Final DataFrame
df.reset_index(drop=True, inplace=True)


/var/folders/h1/t4ps1by94ml46mqx3tjkych80000gn/T/ipykernel_28765/3554801825.py:22: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  normalized_df = pd.concat([normalized_df, normalized_dict], sort=False)
/var/folders/h1/t4ps1by94ml46mqx3tjkych80000gn/T/ipykernel_28765/3554801825.py:22: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  normalized_df = pd.concat([normalized_df, normalized_dict], sort=False)
/var/folders/h1/t4ps1by94ml46mqx3tjkych80000gn/T/ipykernel_28765/3554801825.py:22: FutureWarning: 

In [ ]:
df